# Similarity

### 对于每个公司的文档，计算其与之前一段时间文档的相似度

In [1]:
import re
import jieba
import pandas as pd
import numpy as np
import json
import datetime
from sklearn.feature_extraction import DictVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from Levenshtein import distance, hamming, median
from sklearn.metrics import jaccard_score

### Stop words list

In [2]:
# global variables initialisation
with open('../stop_words/中文停用词表.txt', 'r', encoding='UTF-8-sig') as f:
    stop_words = [ word.strip().replace('\n', '') for word in f.readlines()]
symbols = stop_words[0:26]
print('e.g.', stop_words[23:33])

e.g. ['？', '.', '%', '一', '一些', '一何', '一切', '一则', '一方面', '一旦']


### Data
1. Read the original data; 
2. Merge the existing data with the date information (here step 1 & 2 are specific to the current project, for future use, please make sure the input data contains all the wanted information);

#### Read the original data

In [ ]:
# Single input
data_path = '请输入数据路径'  # e.g. data/record1.xls
all_data = pd.read_excel(data_path)
all_data.info()

In [3]:
# Multiple inputs
# 如果能把所有的record数据都集成一个excel文件，就可以用上面的代码
all_data = pd.DataFrame()
for i in range(17):
    i += 1
    path = "../data/record" + str(i) + ".xls"
    all_data = all_data.append(pd.read_excel(path), sort=False)
all_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 58611 entries, 0 to 693
Data columns (total 13 columns):
文档号码                                58611 non-null int64
证券代码（请务必使用text格式 以保留代码中的0）          30412 non-null object
证券简称                                41984 non-null object
投资者关系活动类别                           41287 non-null object
参与机构数量（家）（0代表0个单位，空白代表无相关信息）        41992 non-null object
参与机构（请用分号隔开，并统一使用证券公司名称（申银万国 等））    30187 non-null object
参与投资者数量                             41987 non-null object
日期（格式统一为xx/xx/xxxx（日月年））            41992 non-null object
接待人员数量                              41992 non-null object
投资者关系活动主要内容介绍                       41986 non-null object
Unnamed: 10                         16619 non-null object
证券代码（请务必使用text格式以保留代码中的0）           11579 non-null object
参与机构（请用分号隔开；并统一使用证券公司名称（申银万国等））     11580 non-null object
dtypes: int64(1), object(12)
memory usage: 6.3+ MB


In [4]:
# 取出想要的数据并且去除空行
wanted_columns = ['文档号码','投资者关系活动主要内容介绍'] 
data = all_data[wanted_columns]
print('Before cleaning:')
print(data.shape)
data = data.dropna() # drop rows with null values
print('After cleaning:')
print(data.shape)

Before cleaning:
(58611, 2)
After cleaning:
(41986, 2)


#### Read the extra date information and merge it with the original data

In [5]:
# 读取日期数据
date_info = pd.read_stata('../data/date.dta')
# 根据文档号码将两份数据合并,并去掉空行
data = pd.merge(data, date_info, on='文档号码')
data = data.dropna()
data.shape

(41961, 5)

In [6]:
data.head(10)

文档号码                                      投资者关系活动主要内容介绍  \
0  1200573239  一、问题回答。\n1、非公开发行的进展情况如何？\n答：目前中国证监会正在审核公司非公开发行...   
1  1200573241  会议主要关注BE部分。\n\n问题一：BE最近有何变化？\n回答：公司目前业务进展顺利，业务...   
2  1200573242  会议主要关注BYD部分。\n\n问题一：公司新能源汽车的目前的进展情况？\n回答：公司将新能...   
3  1200573245  问：请您谈谈公司2015年的收入季节性是否还会存在？\n答：公司2013、2014年的第三季...   
4  1200573285  1、公司目前的出口情况？\n答：近几年来，公司加强了海外出口的投入力度，组建了专门的国际贸易...   
5  1200573318  国联证券研究员于2015年01月22日到公司化工新材料产业园区进行现场调研座谈，主要内容如下...   
6  1200573672  1.公司机床的优势？\n公司具有规模优势，公司是国内机床产品种类最为齐全的机床类企业。具备提...   
7  1200573678  一、签署《调研来访承诺书》；\n二、回答调研提问，主要问答简述如下：\n1、问：公司规划建新...   
8  1200573726  一、交流内容\n董事会秘书：欢迎英大基金来访本公司。投资者和研究人员来访本公司须遵循深圳交易...   
9  1200573767  1、本次收购方式、交易价格及收购资金来源？\n答：公司全资子公司翼鹏投资、公司及公司实际控制...   

    日期格式统一为xxxxxxxx日月年  stkcd    year  
0  2015-01-23 00:00:00   2635  2015.0  
1  2015-01-22 00:00:00   2594  2015.0  
2  2015-01-23 00:00:00   2594  2015.0  
3  2015-01-22 00:00:00   2439  2015.0  
4  2015-01-22 00:00:00   2690  2015.0  
5  2015-01-22 00:00:00    830  2015.0  
6  2015-01-22 00:00:00    410  2015.0  
7  2015-01-23 00:00:00     49  2015.0  
8  2015-01-23 00:00:00   2579  2015.0  
9  2015-01-23 00:00:00   2324  2015.0

In [7]:
# 把公司代号变成category,而不是保留数值意义
data = data.astype({'stkcd' : str})

In [8]:
# Test data, take stkcd 2635
test_data = data[data['stkcd'] == '2635']
test_data.head(5)

文档号码                                      投资者关系活动主要内容介绍  \
0     1200573239  一、问题回答。\n1、非公开发行的进展情况如何？\n答：目前中国证监会正在审核公司非公开发行...   
106   1200590776  一、问题回答。\n1、新星控股（Supernova Holdings (Singapore)...   
202   1200612620  问题回答。\n非公开发行股票项目的进展情况如何？\n答：目前中国证监会正在审核公司非公开发行...   
302   1200632294  问题回答。\n非公开发行股票项目的进展情况如何？\n答：目前中国证监会正在审核公司非公开发行...   
1075  1200961357  问题回答。\n为什么公司2015年一季报中营业收入大幅增长，净利润只是小幅增长？\n答：公司...   

       日期格式统一为xxxxxxxx日月年 stkcd    year  
0     2015-01-23 00:00:00  2635  2015.0  
106   2015-01-29 00:00:00  2635  2015.0  
202   2015-02-05 00:00:00  2635  2015.0  
302   2015-02-12 00:00:00  2635  2015.0  
1075  2015-04-30 00:00:00  2635  2015.0

In [9]:
# 拿到所有unique的公司代号
company_ids = list(pd.unique(data['stkcd']))
print('There are', len(company_ids), 'companies.')

There are 1854 companies.


### Preprocessing

In [10]:
# 数据预处理所需要的所有方法

# clean the document, only Chinese characters, Numbers and Punctuations are left.
def clean(doc):
    chi = r'([\u4E00-\u9FA5]|[0-9]|[“”、。《》！，：；？\.%])'
    pa = re.compile(chi)
    return "".join(re.findall(pa, doc))

# sentence segmentation
def sent_seg(cleaned_doc):
    sent_pa = re.compile(r'.+?[？。！]')
    return re.findall(sent_pa, cleaned_doc)

def pure_sent(sent):
    cleaned_sent_pa = re.compile(r'([\u4E00-\u9FA5])')
    return ''.join(re.findall(cleaned_sent_pa, sent))
        
# Size of a doc is defined as the total number of valid Chinese characters
def raw_process(doc):
    cleaned_doc = clean(doc)
    sents = sent_seg(cleaned_doc)
    if not cleaned_doc or not len(sents):
        return {
            'sents': [],
            'size': 0,
            'avg_sent_len' : 0
        }
    else:
        total_length = sum([len(pure_sent(sent)) for sent in sents])
        avg_sent_length = total_length / len(sents)
        return {
            'sents': sents,
            'size' : total_length,
            'avg_sent_len' : avg_sent_length 
        }

# generate frequency distribution for each document, vital step for bag_of_words representation
def gen_freq_dist(doc):
    stat = raw_process(doc)
    sents = stat['sents']
    freq_dist = dict()
    pa = re.compile(r'([$0123456789?_“”、。《》！，：；？\.%])')
    for sent in sents:
        # calculate sent length after
        words = jieba.cut(sent, cut_all=False, HMM=True)
        for word in words:
            # ignore all the stop words
            if (not word in stop_words) and (not re.findall(pa, word)):
                freq_dist.setdefault(word, 0)
                freq_dist[word] += 1
    return { 'freq_dist' : freq_dist, 
             'size' : stat['size'],
             'avg_sent_len' : stat['avg_sent_len'],
             'n_sents' : len(sents)
           }

### Full frequencey distribution

使用之前已经生成过的all_freq_dist.json文件

In [12]:
with open('all_freq_dist.json', 'r', encoding='UTF-8-sig') as f:
    all_freq_dist = json.load(f)
all_freq_dist_df = pd.DataFrame.from_dict(all_freq_dist, orient='index', columns=['freq'])
print('Most frequent word is: ' + str(np.argmax(all_freq_dist_df['freq'])))
all_freq_dist_df.describe()

Most frequent word is: 公司


freq
count  128918.000000
mean      137.010472
std      2841.917420
min         1.000000
25%         1.000000
50%         3.000000
75%        13.000000
max    770176.000000

### Bag of words construction 
#### (For Cosine Similarity)

有了完整的freq_dist以后就能把每个document都转换成bag_of_words形式。

In [13]:
# 先把frequency低于3的全部去掉
low_freq_words = [word for word in all_freq_dist.keys() if all_freq_dist[word] <= 3]
for lw in low_freq_words:
    del all_freq_dist[lw]
print('Remaining number of words:', len(all_freq_dist.keys()))

Remaining number of words: 59536


In [14]:
vec = DictVectorizer()
all_bow = vec.fit_transform(all_freq_dist).toarray()
print('e.g.', vec.get_feature_names()[12000:12010])

e.g. ['化已', '化建', '化强', '化成', '化整为零', '化新', '化是', '化机', '化机制', '化来']


In [15]:
# generate bag_of_words for each document
def gen_bag_of_words(doc):
    global vec
    return vec.transform(gen_freq_dist(doc)['freq_dist']).toarray()

### Similarity Measures
1. Cosine Similarity: $$\cos(\theta) = \frac{\vec{d_i} \cdot \vec{d_j}}{\|\vec{d_i}\| \|\vec{d_j}\|}$$ where $\vec{d_i}$, $\vec{d_j}$ are bag-of-words representations of document $i$ and $j$, respectively.
2. Jaccard Similarity: $$ J(S_i, S_j) = \frac{|S_i \cap S_j|}{|S_i \cup S_j|}$$, where $S_i$ and $S_j$ are the $\textit{sets}$ of words (hence term frequency does not matter) in document $i$ and $j$, respectively.
3. Minimum Edit Distance: Use dynamic programming to calculate the cost of transformation (insertion:1, deletion:1, substitution:2) from one text to another.

In [108]:
# fix the pivot document, compute the similarities between it and another input document
def compute_similarities(pivot_doc, inp_doc):
      
    # bag-of-words representations specifying term frequencies
    bow_pivot = gen_bag_of_words(pivot_doc)
    bow_inp = gen_bag_of_words(inp_doc)
    # binary indicators
    # [0] because Jaccard similarity requires 1-d array
    ind_pivot = (bow_pivot > 0).astype(int)[0]
    ind_inp = (bow_inp > 0).astype(int)[0]
    
    if(np.sum(ind_pivot) == 0 and np.sum(ind_inp) == 0):
        print('       --- Abandon current input document cause no true lables at all.')
        return {
            'cosine': [None],
            'jaccard': [None],
            'minimum_edit_distance': [None]
        }
    
    # cosine similarity
    cos_sim = cosine_similarity(bow_pivot, bow_inp)[0][0]
    # jaccard similarity
    jac_sim = jaccard_score(ind_pivot, ind_inp)
    # minimum edit distance
    med = distance(clean(pivot_doc), clean(inp_doc))
    
    return {
        'cosine': [cos_sim],
        'jaccard': [jac_sim],
        'minimum_edit_distance': [med] 
    }
    

In [97]:
compute_similarities(test_data.iloc[0][1], test_data.iloc[1][1])

{'cosine': [0.985472685756607],
 'jaccard': [0.9122807017543859],
 'minimum_edit_distance': [175]}

In [98]:
def gen_company_data(company_ID):
    global data
    company_data = data[data['stkcd'] == company_ID]
    # essentital step for time-saving
    company_data = company_data.sort_values(by=['日期格式统一为xxxxxxxx日月年'], ascending=False)
    company_data = company_data.reset_index(drop=True)
    return company_data

gen_company_data('2635').head(5)

文档号码                                      投资者关系活动主要内容介绍  \
0  1204365205  一、公司近况介绍\n1、公司目前的整体业务情况\n公司目前的业务主要包括智能手机、台式电脑、...   
1  1204350097  一、公司近况介绍\n1、公司目前的整体业务情况\n公司目前的业务主要包括智能手机、台式电脑、...   
2  1204327721  一、公司近况介绍\n1、公司目前的整体业务情况\n公司目前的业务主要包括智能手机、台式电脑、...   
3  1204320558  一、公司近况介绍\n1、公司目前的整体业务情况\n公司目前的业务主要包括智能手机、台式电脑、...   
4  1204310751  一、公司近况介绍\n1、公司目前的整体业务情况\n公司目前的业务主要包括智能手机、台式电脑、...   

    日期格式统一为xxxxxxxx日月年 stkcd    year  
0  2018-01-24 00:00:00  2635  2018.0  
1  2018-01-17 00:00:00  2635  2018.0  
2  2018-01-12 00:00:00  2635  2018.0  
3  2018-01-09 00:00:00  2635  2018.0  
4  2018-01-05 00:00:00  2635  2018.0

In [131]:
def for_one_company(company_ID, days=90):
    
    company_data = gen_company_data(company_ID)
    results = pd.DataFrame()
    count = 0
    
    for i, dp_i in company_data.iterrows():
        date_i = dp_i['日期格式统一为xxxxxxxx日月年']
        doc_i = dp_i['投资者关系活动主要内容介绍']
        sims = pd.DataFrame()
        num = 0
        
        # already sorted from the most recent, so traverse only documents below (in the past)
        # and once the date is out of range, there is no need to traverse the rest of the documents
        for j in range(i+1, len(company_data)):
            dp_j = company_data.iloc[j]        
            date_j = dp_j['日期格式统一为xxxxxxxx日月年']
            # process documents within preset days only
            if (date_i - date_j).days <= days:
                doc_j = dp_j['投资者关系活动主要内容介绍']
                sims = sims.append(pd.DataFrame.from_dict(compute_similarities(doc_i, doc_j)))
                num += 1
            else:
                # no need to traverse the rest (at least save half of time, in practice, should be around 10n)
                break
        result = pd.DataFrame(columns=['文档号码', 'cosine_max', 'jaccard_max', \
                                       'med_min', 'cosine_mean', 'jaccard_mean', \
                                       'med_mean', str(days) + '天内文档数量', 'stkcd'])
        result['文档号码'] = [dp_i['文档号码']]
        try:
            result['cosine_max'] = [sims.max().loc['cosine']]
            result['jaccard_max'] = [sims.max().loc['jaccard']]
            result['med_min'] = [sims.min().loc['minimum_edit_distance']]
            result['cosine_mean'] = [sims.mean().loc['cosine']]
            result['jaccard_mean'] = [sims.mean().loc['jaccard']]
            result['med_mean'] = [sims.mean().loc['minimum_edit_distance']]
            result[str(days) + '天内文档数量'] = num
            result['stkcd'] = company_ID
            print("[Company " + str(company_ID) + "][" + str(count) + "]", \
              "Document", str(dp_i['文档号码']), "has been processed,", \
              str(num), 'documents withinin past', str(days), 'days')
        except:
            result['cosine_max'] = None
            result['jaccard_max'] = None
            result['med_min'] = None
            result['cosine_mean'] = None
            result['jaccard_mean'] = None
            result['med_mean'] = None
            result[str(days) + '天内文档数量'] = num
            result['stkcd'] = company_ID
            print("[Company " + str(company_ID) + "][" + str(count) + "]", \
              "Document", str(dp_i['文档号码']), "cannot be processed,")
            
        results = results.append(result)
        count += 1
        
        #if count == 3:
            #break

    return results.reset_index(drop=True)

In [132]:
# Main execution
all_scores = pd.DataFrame()
for company_ID in company_ids:
    print('Processing documents of company', str(company_ID))
    all_scores = all_scores.append(for_one_company(company_ID, days=90), ignore_index=True)

        

Processing documents of company 2635
[Company 2635][0] Document 1204365205 has been processed, 10 documents withinin past 90 days
[Company 2635][1] Document 1204350097 has been processed, 9 documents withinin past 90 days
[Company 2635][2] Document 1204327721 has been processed, 8 documents withinin past 90 days
[Company 2635][3] Document 1204320558 has been processed, 7 documents withinin past 90 days
[Company 2635][4] Document 1204310751 has been processed, 6 documents withinin past 90 days
[Company 2635][5] Document 1204271855 has been processed, 5 documents withinin past 90 days
[Company 2635][6] Document 1204199626 has been processed, 6 documents withinin past 90 days
[Company 2635][7] Document 1204150680 has been processed, 8 documents withinin past 90 days
[Company 2635][8] Document 1204138926 has been processed, 7 documents withinin past 90 days
[Company 2635][9] Document 1204108769 has been processed, 7 documents withinin past 90 days
[Company 2635][10] Document 1204095182 has

[Company 2635][88] Document 1200355546 has been processed, 2 documents withinin past 90 days
[Company 2635][89] Document 1200272580 has been processed, 1 documents withinin past 90 days
[Company 2635][90] Document 1200189219 cannot be processed,
[Company 2635][91] Document 64006637 has been processed, 2 documents withinin past 90 days
[Company 2635][92] Document 63591152 has been processed, 2 documents withinin past 90 days
[Company 2635][93] Document 63568224 has been processed, 1 documents withinin past 90 days
[Company 2635][94] Document 63443143 has been processed, 3 documents withinin past 90 days
[Company 2635][95] Document 63264155 has been processed, 6 documents withinin past 90 days
[Company 2635][96] Document 63241185 has been processed, 5 documents withinin past 90 days
[Company 2635][97] Document 63225602 has been processed, 4 documents withinin past 90 days
[Company 2635][98] Document 63095245 has been processed, 6 documents withinin past 90 days
[Company 2635][99] Documen

       --- Abandon current input document cause no true lables at all.
       --- Abandon current input document cause no true lables at all.
       --- Abandon current input document cause no true lables at all.
       --- Abandon current input document cause no true lables at all.
       --- Abandon current input document cause no true lables at all.
[Company 2594][13] Document 1204195845 has been processed, 37 documents withinin past 90 days
[Company 2594][14] Document 1204195499 has been processed, 36 documents withinin past 90 days
[Company 2594][15] Document 1204195474 has been processed, 35 documents withinin past 90 days
[Company 2594][16] Document 1204195438 has been processed, 34 documents withinin past 90 days
       --- Abandon current input document cause no true lables at all.
       --- Abandon current input document cause no true lables at all.
       --- Abandon current input document cause no true lables at all.
       --- Abandon current input document cause no true 

[Company 2594][55] Document 1203722020 has been processed, 15 documents withinin past 90 days
[Company 2594][56] Document 1203694901 has been processed, 14 documents withinin past 90 days
[Company 2594][57] Document 1203694898 has been processed, 13 documents withinin past 90 days
[Company 2594][58] Document 1203694877 has been processed, 12 documents withinin past 90 days
[Company 2594][59] Document 1203693585 has been processed, 11 documents withinin past 90 days
[Company 2594][60] Document 1203693584 has been processed, 10 documents withinin past 90 days
[Company 2594][61] Document 1203574101 has been processed, 9 documents withinin past 90 days
[Company 2594][62] Document 1203574102 has been processed, 8 documents withinin past 90 days
[Company 2594][63] Document 1203574100 has been processed, 8 documents withinin past 90 days
       --- Abandon current input document cause no true lables at all.
       --- Abandon current input document cause no true lables at all.
[Company 2594][

[Company 2594][130] Document 1202373081 has been processed, 19 documents withinin past 90 days
       --- Abandon current input document cause no true lables at all.
       --- Abandon current input document cause no true lables at all.
       --- Abandon current input document cause no true lables at all.
[Company 2594][131] Document 1202373080 has been processed, 18 documents withinin past 90 days
[Company 2594][132] Document 1202336476 has been processed, 17 documents withinin past 90 days
[Company 2594][133] Document 1202334999 has been processed, 16 documents withinin past 90 days
       --- Abandon current input document cause no true lables at all.
       --- Abandon current input document cause no true lables at all.
[Company 2594][134] Document 1202335000 has been processed, 15 documents withinin past 90 days
[Company 2594][135] Document 1202335001 has been processed, 14 documents withinin past 90 days
       --- Abandon current input document cause no true lables at all.
[Com

...

[Company 810][14] Document 1201222860 has been processed, 8 documents withinin past 90 days
[Company 810][15] Document 1201172380 has been processed, 7 documents withinin past 90 days
[Company 810][16] Document 1201157272 has been processed, 6 documents withinin past 90 days
[Company 810][17] Document 1201121321 has been processed, 5 documents withinin past 90 days
[Company 810][18] Document 1201059936 has been processed, 4 documents withinin past 90 days
[Company 810][19] Document 1200978038 has been processed, 4 documents withinin past 90 days
[Company 810][20] Document 1200835989 has been processed, 4 documents withinin past 90 days
[Company 810][21] Document 1200824200 has been processed, 3 documents withinin past 90 days
[Company 810][22] Document 1200809224 has been processed, 2 documents withinin past 90 days
[Company 810][23] Document 1200628444 has been processed, 1 documents withinin past 90 days
[Company 810][24] Document 1200609044 cannot be processed,
Processing documents 

[Company 300435][7] Document 1201174205 cannot be processed,
Processing documents of company 760
[Company 760][0] Document 1201230017 cannot be processed,
Processing documents of company 300478
[Company 300478][0] Document 1202473748 has been processed, 2 documents withinin past 90 days
[Company 300478][1] Document 1202362699 has been processed, 1 documents withinin past 90 days
[Company 300478][2] Document 1202338237 cannot be processed,
[Company 300478][3] Document 1201853518 cannot be processed,
[Company 300478][4] Document 1201357026 cannot be processed,
Processing documents of company 68
[Company 68][0] Document 1202337575 cannot be processed,
[Company 68][1] Document 1201437264 cannot be processed,
Processing documents of company 300479
[Company 300479][0] Document 1203315030 cannot be processed,
[Company 300479][1] Document 1202846771 has been processed, 1 documents withinin past 90 days
[Company 300479][2] Document 1202816160 cannot be processed,
[Company 300479][3] Document 12

[Company 2796][2] Document 1202453515 has been processed, 3 documents withinin past 90 days
[Company 2796][3] Document 1202388115 has been processed, 2 documents withinin past 90 days
[Company 2796][4] Document 1202352629 has been processed, 1 documents withinin past 90 days
[Company 2796][5] Document 1202334593 cannot be processed,
Processing documents of company 2765
[Company 2765][0] Document 1203964191 cannot be processed,
[Company 2765][1] Document 1203298252 cannot be processed,
[Company 2765][2] Document 1202898388 has been processed, 1 documents withinin past 90 days
[Company 2765][3] Document 1202855551 has been processed, 1 documents withinin past 90 days
[Company 2765][4] Document 1202691087 has been processed, 2 documents withinin past 90 days
[Company 2765][5] Document 1202469876 has been processed, 2 documents withinin past 90 days
[Company 2765][6] Document 1202468218 has been processed, 1 documents withinin past 90 days
[Company 2765][7] Document 1202343441 cannot be pr

[Company 300601][5] Document 1204102789 has been processed, 4 documents withinin past 90 days
[Company 300601][6] Document 1203974849 has been processed, 4 documents withinin past 90 days
[Company 300601][7] Document 1203971313 has been processed, 3 documents withinin past 90 days
[Company 300601][8] Document 1203906880 has been processed, 2 documents withinin past 90 days
[Company 300601][9] Document 1203758221 has been processed, 1 documents withinin past 90 days
[Company 300601][10] Document 1203721564 cannot be processed,
[Company 300601][11] Document 1203150953 cannot be processed,
Processing documents of company 300616
[Company 300616][0] Document 1204351518 has been processed, 6 documents withinin past 90 days
[Company 300616][1] Document 1204327720 has been processed, 6 documents withinin past 90 days
[Company 300616][2] Document 1204316637 has been processed, 5 documents withinin past 90 days
[Company 300616][3] Document 1204213854 has been processed, 7 documents withinin past

Processing documents of company 2860
[Company 2860][0] Document 1204327719 has been processed, 2 documents withinin past 90 days
[Company 2860][1] Document 1204144554 has been processed, 3 documents withinin past 90 days
[Company 2860][2] Document 1204125360 has been processed, 3 documents withinin past 90 days
[Company 2860][3] Document 1204004347 has been processed, 2 documents withinin past 90 days
[Company 2860][4] Document 1203919913 has been processed, 4 documents withinin past 90 days
[Company 2860][5] Document 1203790837 has been processed, 3 documents withinin past 90 days
[Company 2860][6] Document 1203638829 has been processed, 2 documents withinin past 90 days
[Company 2860][7] Document 1203641158 has been processed, 1 documents withinin past 90 days
[Company 2860][8] Document 1203615892 cannot be processed,
Processing documents of company 2867
[Company 2867][0] Document 1204359802 has been processed, 9 documents withinin past 90 days
[Company 2867][1] Document 1204337048 h

In [135]:
all_scores.to_excel('similarity_90_days.xlsx')